# Modifying evendrow/INQUIRE-Rerank

This notebook will modify evendrow/INQUIRE-Rerank to add a query id. This will help in scoring our Image Search system.

**INQUIRE:**
- Paper: https://arxiv.org/pdf/2411.02537
- Github Repo: https://github.com/inquire-benchmark/INQUIRE
- Homepage: https://inquire-benchmark.github.io/
- Dataset: https://github.com/inquire-benchmark/INQUIRE/tree/main/data/

## Prerequisites

In [ ]:
%pip install datasets
%pip install huggingface_hub

In [10]:
from datasets import load_dataset, DatasetDict
import numpy as np
from huggingface_hub import HfApi

## 1. Load the Dataset

If you are using Google collab, remember to set the secret `HF_TOKEN`.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.

In [11]:
# Load your dataset from Hugging Face
dataset = load_dataset("evendrow/INQUIRE-Rerank")

## 2. Collect all Unique Queries acrross ALL splits

In [4]:
all_queries = set()
for split in dataset.keys():
    all_queries.update(dataset[split]["query"])

## 2. Generate Unique IDs for Each Query

We can create a mapping of each unique query to an incremental ID.

In [12]:
def add_query_id_column(examples):
    """Function to add `query_id` to each dataset split"""
    examples["query_id"] = [query_to_id[q] for q in examples["query"]]
    return examples

# Assign each unique query a unique integer ID
query_to_id = {query: idx for idx, query in enumerate(sorted(all_queries))}

# Apply transformation to all splits and wrap in DatasetDict
dataset = DatasetDict({
    split: dataset[split].map(add_query_id_column, batched=True)
    for split in dataset.keys()
})

In [13]:
# Print sample to verify
print(dataset["validation"][0])

{'image': <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=375x500 at 0x7E81541F7F10>, 'query': 'leopard on a road', 'relevant': 1, 'clip_score': 0.333251953125, 'inat24_image_id': 2821516, 'inat24_file_name': 'train/04684_Animalia_Chordata_Mammalia_Carnivora_Felidae_Panthera_pardus/03407823-c7e0-4a8c-b2f7-1bf9e6baa422.jpg', 'supercategory': 'Context', 'category': 'Human Impact', 'iconic_group': 'Mammals', 'inat24_species_id': 4684, 'inat24_species_name': 'Panthera pardus', 'latitude': 21.2294656384, 'longitude': 73.587988585, 'location_uncertainty': 30396.0, 'date': '2022-11-21 16:02:00+00:00', 'license': 'CC BY-NC 4.0', 'rights_holder': 'Neel Prajapati', 'query_id': 169}


In [14]:
# Print sample to verify
print(dataset["test"][0])

{'image': <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=500x400 at 0x7E81543022D0>, 'query': 'A mongoose standing upright alert', 'relevant': 1, 'clip_score': 0.360595703125, 'inat24_image_id': 953152, 'inat24_file_name': 'train/04687_Animalia_Chordata_Mammalia_Carnivora_Herpestidae_Urva_auropunctata/05d10a77-bf97-467e-9535-d0016894d228.jpg', 'supercategory': 'Behavior', 'category': 'Defensive and Survival Behaviors', 'iconic_group': 'Mammals', 'inat24_species_id': 4687, 'inat24_species_name': 'Urva auropunctata', 'latitude': 19.7241106, 'longitude': -155.0868193, 'location_uncertainty': 10248.0, 'date': '2021-08-29 20:58:00+00:00', 'license': 'CC BY-NC 4.0', 'rights_holder': 'Monika Wood', 'query_id': 11}


## 3. Push the Modified Dataset to Hugging Face

Finally we push the dataset to our organization.

In [16]:
repo_id = "sagecontinuum/INQUIRE-Benchmark-small"

# Push the dataset
dataset.push_to_hub(repo_id)

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Map:   0%|          | 0/4000 [00:00<?, ? examples/s]

Creating parquet from Arrow format:   0%|          | 0/40 [00:00<?, ?ba/s]

Uploading the dataset shards:   0%|          | 0/4 [00:00<?, ?it/s]

Map:   0%|          | 0/4000 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/4000 [00:00<?, ? examples/s]

Creating parquet from Arrow format:   0%|          | 0/40 [00:00<?, ?ba/s]

Map:   0%|          | 0/4000 [00:00<?, ? examples/s]

Creating parquet from Arrow format:   0%|          | 0/40 [00:00<?, ?ba/s]

CommitInfo(commit_url='https://huggingface.co/datasets/sagecontinuum/INQUIRE-Benchmark-small/commit/9f39d29d2cf983d3781857462afcc8390fa22715', commit_message='Upload dataset', commit_description='', oid='9f39d29d2cf983d3781857462afcc8390fa22715', pr_url=None, repo_url=RepoUrl('https://huggingface.co/datasets/sagecontinuum/INQUIRE-Benchmark-small', endpoint='https://huggingface.co', repo_type='dataset', repo_id='sagecontinuum/INQUIRE-Benchmark-small'), pr_revision=None, pr_num=None)

## Citation

```
@article{vendrow2024inquire,
  title={INQUIRE: A Natural World Text-to-Image Retrieval Benchmark},
  author={Vendrow, Edward and Pantazis, Omiros and Shepard, Alexander and Brostow, Gabriel and Jones, Kate E and Mac Aodha, Oisin and Beery, Sara and Van Horn, Grant},
  journal={NeurIPS},
  year={2024},
}
```